In [46]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import Span
from shapely.geometry import Point
import geopandas as gpd
import glob
import bokeh
from datetime import datetime
from bokeh.layouts import column
from bokeh.models import Legend, Tabs, TabPanel
from bokeh.core.validation.warnings import MISSING_RENDERERS, EMPTY_LAYOUT

# Set fonts for matplotlib
plt.rcParams["font.family"] = "Arial"
plt.rcParams["font.size"] = 14

In [47]:

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(EMPTY_LAYOUT, True)

{Warning(code=1002, name='EMPTY_LAYOUT', description='Layout has no children')}

In [48]:
# Function to convert a pandas dataframe to a geopandas dataframe
def convert_to_gdf(df):
    geometry = [Point(xy) for xy in zip(df.longitude, df.latitude)]
    gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry=geometry)

    return gdf

# Sri Lanka – Flooding and Cyclone

For this analysis, two datasets are utilized:

### 1. Southwest Monsoon Flood Business Activity Trends Dataset

The dataset triggered by the **Southwest Monsoon Flood** contains daily data from **June 7th, 2024 to June 16th, 2024**.

The baseline date for this dataset is **April 23rd, 2024** (45 days before the crisis).


### 2. Cyclone Fengal Business Activity Trends Dataset

The dataset triggered by **Cyclone Fengal** contains daily data from **December 2nd, 2024 to December 16th, 2024**.

The baseline date for this dataset is **October 18th, 2024** (45 days before the crisis). 

In [49]:
# Read shapefiles from HdX UNOCHA
lka_adm2 = gpd.read_file(
    "../../data/lka_adm_20220816_shp/lka_admbnda_adm2_slsd_20220816.shp"
)
lka_adm1 = gpd.read_file(
    "../../data/lka_adm_20220816_shp/lka_admbnda_adm1_slsd_20220816.shp"
)

### Data Information Summary

This dataset provides insights into business activity at the [GADM 2](https://gadm.org/) level, covering 25 districts in Sri Lanka

#### **Activity Quantile (activity_quantile):**
The activity quantile metric is used to measure changes in Business Activity.

- **Purpose:** Measures changes in business activity relative to a baseline period.  
- **Key Values:**
  - **0.5:** Normal activity (baseline level).  
  - **Above 0.5:** Increased activity.  
  - **Below 0.5:** Decreased activity.  

#### **Calculation Overview:**
1. Compare daily activity of business pages to their baseline activity levels (quantiles).  
2. Aggregate and standardize these values to follow a normal distribution.  
3. Apply a cumulative probability transformation to derive a value between **0 and 1**.  
4. Average results over 7 days to reduce daily noise.  
5. Provides equal weight to all businesses, avoiding bias from more active pages. 


In [50]:
businessActivity2024 = pd.read_csv("../../data/business-activity-trends/raw/bangladesh-india-sri_lanka-business-activity-trends-crisis-20240509-20241216.csv")
# filter country == LKA
businessActivity2024 = businessActivity2024[businessActivity2024["country"] == "LKA"]


In [51]:
# Convert columns to datetime

businessActivity2024["ds"] = businessActivity2024["ds"].apply(
    lambda x: pd.to_datetime(x)
)

In [52]:
import unicodedata

# Rename columns from shapefile to match activity data
lka_adm2 = lka_adm2.rename(columns={"ADM2_EN": "polygon_name"})
lka_adm2["polygon_name"] = lka_adm2["polygon_name"].str.upper()

# Rename columns from flood data to match activity data
businessActivity2024 = businessActivity2024.rename(columns={"Admin2": "polygon_name"})
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].str.upper()

In [53]:
# Get the unique business verticals 
business_verticals = list(businessActivity2024["business_vertical"].unique())

print(
    f"Sri Lanka's Political Crisis Business Actvity Trends has the following business verticals {business_verticals}"
)

Sri Lanka's Political Crisis Business Actvity Trends has the following business verticals ['Retail', 'Local Events', 'Public Good', 'All', 'Business & Utility Services', 'Restaurants', 'Travel', 'Grocery & Convenience Stores', 'Professional Services', 'Home Services', 'Manufacturing', 'Lifestyle Services', nan]


In [54]:
from bokeh.models import Div, Span, Label
from bokeh.layouts import column

def get_line_plot(
    businessActivity,
    title,
    source,
    subtitle=None,
    vertical_dates=None,
    vertical_labels=None,
    limitations_note=None,  # Add note parameter
    label_offset=10  # Offset for labels to the right
):
    # Create the main figure
    p2 = figure(
        x_axis_type="datetime", 
        width=1000, 
        height=600, 
        toolbar_location="above",
        sizing_mode="stretch_width"  
    )
    p2.add_layout(Legend(), "right")

    # Define a color palette 
    from bokeh.palettes import Category20
    color_palette = Category20[15]  

    # Plot lines for each business vertical
    for id, business_vertical in enumerate(businessActivity["business_vertical"].unique()):
        if pd.isnull(business_vertical):  # Handle missing values in business_vertical
            business_vertical = "Unknown"

        business_vertical = str(business_vertical)  # Ensure it's a string

        df = businessActivity[businessActivity["business_vertical"] == business_vertical][
            ["ds", "activity_quantile"]
        ].reset_index(drop=True)

        p2.line(
            df["ds"],
            df["activity_quantile"],
            line_width=2,
            line_color=color_palette[id % len(color_palette)],  # Handle color overflow
            legend_label=business_vertical,
        )

    # Configure legend
    p2.legend.click_policy = "hide"
    p2.legend.label_text_font_size = "10pt"

    # Horizontal line at 0.5
    baseline = Span(
        location=0.5, 
        dimension="width", 
        line_color="black", 
        line_dash="dashed", 
        line_width=2
    )
    p2.add_layout(baseline)

    # Add vertical lines and labels if provided
    if vertical_dates and vertical_labels:
        for date, label_text in zip(vertical_dates, vertical_labels):
            vline = Span(location=date.timestamp() * 1000, 
                         dimension="height", 
                         line_color="grey", 
                         line_width=1.5, 
                         line_dash="dashed")
            
            p2.add_layout(vline)
            
            label = Label(
                x=date.timestamp() * 1000 + label_offset,  # Adjust to the right
                y=0.7,  # Example y position, adjust as needed
                text=label_text,
                text_color="grey",
                text_font_size="7pt"
            )
            p2.add_layout(label)

    # Use Div for title and subtitle
    title_div = Div(
        text=f"<h2>{title}</h2>", 
        styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"}
    )
    subtitle_div = Div(
        text=f"<p><em>{subtitle}</em></p>" if subtitle else "",
        styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"}
    )
    source_div = Div(
        text=f"<p><small>{source}</small></p>",
        styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"}
    )

    # Add limitations note if provided
    note_div = None
    if limitations_note:
        note_div = Div(
            text=f"""
            <div style="
                background-color: #f9f9f9; 
                border: 1px solid #dddddd; 
                padding: 10px; 
                border-radius: 5px;
                font-size: 12pt;
                margin-top: 10px;
                max-width: 800px;  /* Limit the width of the note */
                word-wrap: break-word;  /* Ensure text wraps within the width */
            ">
                <strong>Note:</strong> {limitations_note}
            </div>
            """,
        )

    # Combine all elements
    layout_elements = [title_div, subtitle_div, p2, source_div]
    if note_div:
        layout_elements.append(note_div)

    layout = column(*layout_elements)

    return layout


### 📊 Analysis by Business Vertical

This section explores how different **business sectors** were impacted during each crisis event.

In [55]:
from bokeh.models import Div, Panel, Tabs
from bokeh.plotting import output_notebook, show
from bokeh.layouts import column

# Activate notebook output
output_notebook()

df_flood_total = (
    businessActivity2024.groupby(["country", "business_vertical", "ds"])
    .mean("activity_quantile")[["activity_quantile"]]
    .reset_index()
)

# filter dates 2024-06-07 to 2024-06-16
df_flood = df_flood_total[
    (df_flood_total["ds"] >= "2024-06-07") & (df_flood_total["ds"] <= "2024-06-16")
]

# filter dates 2024-12-02 to 2024-12-16

df_cyclone = df_flood_total[
    (df_flood_total["ds"] >= "2024-12-02") & (df_flood_total["ds"] <= "2024-12-16")
]

# Create a how to read it tab
def get_explanation_tab():
    """Create a tab explaining how to read the chart."""
    title_div = Div(
        text="<h2>How to read it?</h2>",
        styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"}
    )
    
    explanation_div = Div(
        text="""
        <p>This chart visualizes <strong>Business Activity Trends</strong> during the flood events compared to a 45-day pre-crisis baseline. 
        The metric used is the <em>Activity Quantile</em>, which compares daily activity levels to the baseline period.</p>
        <p><strong>Key Interpretation:</strong></p>
        <ul>
          <li>A value of <strong>0.5</strong> represents <em>normal</em> or <em>baseline-like</em> activity levels, typical of the pre-crisis period.</li>
          <li>Values <strong>above 0.5</strong> indicate increased business activity, showing a higher level of posts compared to the baseline.</li>
          <li>Values <strong>below 0.5</strong> indicate decreased business activity, suggesting lower activity levels relative to the baseline.</li>
        </ul>
        <p>The horizontal dashed line at <strong>0.5</strong> serves as a reference point for normal activity. Any significant deviation from this line highlights anomalous trends in business activity.</p>
        <p>Each colored line represents a different business vertical, allowing a comparative view of sectoral impacts during the crisis.</p>
        <hr>
        <p><strong>Limitations:</strong></p>
        <p>This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. 
        The methodology assumes that businesses post more frequently on Facebook when they are open and less frequently when they are closed. While this allows for insights into disruptions and recovery patterns, these assumptions may not hold true in all contexts. 
        For example, if businesses are posting about the ongoing crisis rather than regular operations, this could be interpreted as increased activity, potentially leading to misleading conclusions about their operational status.</p>
        """,
        styles={"text-align": "left", "font-size": "12pt"}
    )
    
    layout = column(title_div, explanation_div)
    return layout


# Create the tabs
tabs = []

# Tab 1: Cyclone Remal
tabs.append(
    TabPanel(
        child=get_line_plot(
            df_cyclone, 
            "Business Activity (June 7th, 2024 - June 16th, 2024)",
            "Source: Data for Good, Meta",
            subtitle="National average compared to 45 days prior baseline (April 23rd, 2024)", 
            limitations_note="This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. The methodology assumes businesses post more when open, which may not always be accurate."
        ),
        title="Southwest Monsoon Flood",
    )
)

# Tab 2: Flood Crisis
tabs.append(
    TabPanel(
        child=get_line_plot(
            df_flood, 
            "Business Activity (December 2nd, 2024 - December 16th, 2024)",
            "Source: Data for Good, Meta",
            subtitle="National average compared to 45 days prior baseline (October 18th, 2024)",
           # vertical_dates=[datetime(2024, 8, 25), datetime(2024, 8, 29)],  # Example dates for vertical lines
           # vertical_labels=["Rains from 08/21", "End of Flood"],  # Labels for the lines
            label_offset=0,  # Adjusts label position to the right
            limitations_note="This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. The methodology assumes businesses post more when open, which may not always be accurate."
        ),
        title="Cyclone Fengal",
    )
)

# Add the explanation tab
tabs.append(
    TabPanel(
        child=get_explanation_tab(),
        title="How to read it?",
    )
)

# Display the tabs
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)


Loading BokehJS ...

In [56]:
import unicodedata

# Rename columns from shapefile to match activity data
lka_adm2 = lka_adm2.rename(columns={"ADM2_EN": "polygon_name"})
lka_adm2["polygon_name"] = lka_adm2["polygon_name"].str.upper()

# Rename columns from flood data to match activity data
businessActivity2024 = businessActivity2024.rename(columns={"Admin2": "polygon_name"})
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].str.upper()




### Analyzing Changes in Business Activity by Region and Vertical

In [57]:
# Prepare datasets
lka_adm2["key"] = 1
businessActivity2024["key"] = 1

# Standardize names
lka_adm2["polygon_name"] = lka_adm2["polygon_name"].str.upper()
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].str.upper()

#  Merge full business activity with admin boundaries
lka_adm2_repeated = pd.merge(
    lka_adm2.drop(columns=["geometry"]),
    businessActivity2024,
    on=["key", "polygon_name"],
    how="inner"
)

lka_adm2_repeated = pd.merge(
    lka_adm2_repeated,
    lka_adm2[["polygon_name", "geometry"]],
    on="polygon_name",
    how="left"
)

# Convert to GeoDataFrame
lka_adm2_merged_all = gpd.GeoDataFrame(lka_adm2_repeated, geometry="geometry", crs=lka_adm2.crs)

#  Subset by date range for each event

lka_adm2_merged_flood = lka_adm2_merged_all[
    (lka_adm2_merged_all["ds"] >= "2024-06-07") & (lka_adm2_merged_all["ds"] <= "2024-06-16")
].copy()

lka_adm2_merged_cyclone = lka_adm2_merged_all[
    (lka_adm2_merged_all["ds"] >= "2024-12-02") & (lka_adm2_merged_all["ds"] <= "2024-12-16")
].copy()



In [58]:
def map_plot(data, date=None, column_name="activity_quantile", title=None, source=None, subtitle=None):
    # Get districts with data for the date
    if date:
        data_for_date = data[data["ds"] == date]
    else:
        data_for_date = data

    background = lka_adm2.copy()

    # Set up color scale
    cmap = cm.RdYlGn if column_name == "activity_quantile" else cm.Reds
    norm = TwoSlopeNorm(vmin=0, vcenter=0.5, vmax=1) if column_name == "activity_quantile" else Normalize(vmin=0, vmax=data_for_date[column_name].max())

    fig, ax = plt.subplots(figsize=(7, 6)) 

    # Plot full boundaries in light gray
    background.boundary.plot(ax=ax, linewidth=0.5, color="lightgray")

    # Plot active districts with data
    data_for_date.plot(
        column=column_name,
        cmap=cmap,
        norm=norm,
        linewidth=0.8,
        ax=ax,
        edgecolor="white",
        legend=True,
        legend_kwds={"label": column_name.replace("_", " ").title(), "orientation": "vertical"},
    )

    # Add title/subtitle/source
    if title:
        ax.set_title(title, fontsize=14, fontweight="bold")
    if subtitle:
        fig.text(0.5, 0.93, subtitle, ha='center', fontsize=12, style='italic')
    if source:
        fig.text(0.5, 0.01, source, ha='center', fontsize=10, style='italic')

    ax.axis("off")
    buf = BytesIO()
    plt.savefig(buf, format="png", bbox_inches="tight")
    plt.close(fig)
    buf.seek(0)

    return base64.b64encode(buf.read()).decode("utf-8")

### 🗺️ Analysis by Event and Region

The following maps present the analysis at **Admin Level 2** for each event.

For each event, the maps include:
- A **summary of key dates** and impacts,
- **Relevant links** to external sources or reports,
- A **map showing total business activity** during the event period.

These visualizations aim to provide a localized view of how business activity was affected across different regions during key crisis events.

#### Southwest Monsoon Flood Business Activity Trends Dataset

This map visualizes **business activity trends** following the **Southwest Monsoon Floods** in Sri Lanka (May–June 2024), offering insights into economic disruptions and recovery patterns across affected regions.

**Crisis Impact Overview – May–June 2024**

Beginning in **mid-May 2024**, heavy monsoon rains led to **widespread flooding and landslides** across Sri Lanka. The situation escalated in early June, particularly affecting the **southern and western provinces**. Thousands of people were displaced, homes were damaged, and key infrastructure—such as roads, transport, and agricultural land—was severely impacted. 

The floods also disrupted access to basic services and posed **public health risks**, especially in areas already experiencing **dengue outbreaks**.

**Key Dates:**
- **Mid-May 2024**: Onset of heavy monsoon rains  
- **June 1–16, 2024**: Peak flooding and landslide impacts  
- **June 12 onward**: Continued rainfall forecast across affected regions

**Key Places Affected:**
- **Western Province**: including **Colombo, Kalutara, Gampaha**  
- **Southern Province**: including **Matara, Galle**  
- **Sabaragamuwa Province**: including **Ratnapura, Kegalle**  
- **Central Highlands**: including **Nuwara Eliya**


See more details in the [SRI LANKA Flooding in South and West: Crisis Impact Overview](https://www.acaps.org/fileadmin/Data_Product/Main_media/20240612_ACAPS_Anticipatory_note_Sri_Lanka_Flooding.pdf)




In [59]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64
from bokeh.io import show
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook

# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> during the Southwest Monsoon compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The first two tabs show the percentage of the area and population affected by the flood by admin region 2.</li>
          <li>The rest of the tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
          <li>Flood Percentage indicates how much of the region was affected by flooding.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-06-07", "2024-06-09", "2024-06-11" ,"2024-06-13", "2024-06-16"]
data_source = lka_adm2_merged_flood  # Replace with actual data source

# Create tabs list
tabs = []

# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline during the Sri Lanka Flood"
            ),
            title=f"Activity Quantile ({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)



Loading BokehJS ...

#### Cyclone Fengal Business Activity Trends Dataset

This map visualizes **business activity trends** following **Cyclone Fengal** in Sri Lanka (December 2024), highlighting the economic disruptions and recovery patterns resulting from the storm.

**Crisis Impact Overview – December 2024**

In early December 2024, **Cyclone Fengal** impacted parts of Sri Lanka, bringing **strong winds, heavy rainfall, and coastal flooding**. The cyclone disrupted daily life and affected key infrastructure and economic activities, especially in **low-lying and coastal regions**.

The storm caused **localized flooding**, temporary **power outages**, and interruptions to **transport and commercial activity**. Agricultural areas and small businesses were also affected, particularly in regions vulnerable to seasonal cyclones.

**Key Dates:**
- **December 2–16, 2024**: Period of observed storm-related impacts on business activity and infrastructure

**Key Places Affected:**
- **Northern and Eastern coastal districts**: Experienced strong winds and localized flooding  
- **Urban and peri-urban areas**: Observed moderate disruptions to business services, retail activity, and supply chains  
- **Agricultural zones**: Faced flood-related delays and losses during harvesting and transport

**Sources:**
- [IFRC – Cyclone Fengal Response](https://reliefweb.int/disaster/tc-2024-000219-lka)


In [60]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64
from bokeh.io import show
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook

# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> during the Cyclone Fengal compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The rest of the tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
          <li>Flood Percentage indicates how much of the region was affected by flooding.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-12-02", "2024-12-04", "2024-12-06", "2024-12-10", "2024-12-13"]
data_source = lka_adm2_merged_cyclone  # Replace with actual data source

# Create tabs list
tabs = []

# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline during the Sri Lanka Flood"
            ),
            title=f"Activity Quantile ({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...